# Import Libraries

In [90]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option("display.max_columns", None)
pd.set_option("display.max_rows", None)

import json # library to handle JSON files

!pip install geopy
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests

!pip install bs4
from bs4 import BeautifulSoup # library to parse HTML and XML documents

from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

import folium # map rendering library

!pip install lxml

print("Libraries imported.")

Libraries imported.


# Scrap Data from Wiki and create a Data Frame

In [2]:
#scrapping neighborhoods in Canada
url  = "https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M"
page = requests.get(url)
if page.status_code == 200:
    print('Page download successful')
else:
    print('Page download error. Error code: {}'.format(page.status_code))

Page download successful


In [3]:
df_html = pd.read_html(url, header=0, na_values = ['Not assigned'])[0]
df_html.head()

Postal Code           Borough               Neighborhood
0         M1A               NaN                        NaN
1         M2A               NaN                        NaN
2         M3A        North York                  Parkwoods
3         M4A        North York           Victoria Village
4         M5A  Downtown Toronto  Regent Park, Harbourfront

In [4]:
#Drop the the rows on which the Borough is empty
df_html.dropna(subset=['Borough'], inplace=True)

In [8]:
#Group by Postcode / Borough
df_postcodes = df_html.groupby(['Postal Code','Borough']).Neighborhood.agg([('Neighborhood', ', '.join)])
df_postcodes.reset_index(inplace=True)
df_postcodes.head(5)

Postal Code      Borough                            Neighborhood
0         M1B  Scarborough                          Malvern, Rouge
1         M1C  Scarborough  Rouge Hill, Port Union, Highland Creek
2         M1E  Scarborough       Guildwood, Morningside, West Hill
3         M1G  Scarborough                                  Woburn
4         M1H  Scarborough                               Cedarbrae

In [9]:
#Drop the the rows on which the Borough is empty
df_html.dropna(subset=['Borough'], inplace=True)

In [11]:
#Check Neighborhood is empty but Borough exists
n_empty_neighborhood = df_html[df_html['Neighborhood'].isna()].shape[0]
print('Number of rows on which Neighborhood column is empty: {}'.format(n_empty_neighborhood))

Number of rows on which Neighborhood column is empty: 0


In [12]:
print('The shape of the dataset is:',df_postcodes.shape)

The shape of the dataset is: (103, 3)


In [13]:
#to make it easier, we will store this in csv format.
#Export to .CSV
df_postcodes.to_csv('Toronto_Postcodes.csv')

In [14]:
#Read CSV file from link and load into dataframe
url_csv = 'http://cocl.us/Geospatial_data'
df_coordinates = pd.read_csv(url_csv)
df_coordinates.head()

Postal Code   Latitude  Longitude
0         M1B  43.806686 -79.194353
1         M1C  43.784535 -79.160497
2         M1E  43.763573 -79.188711
3         M1G  43.770992 -79.216917
4         M1H  43.773136 -79.239476

In [15]:
#use the previously cleaned data
df_neighborhoods = pd.read_csv('Toronto_Postcodes.csv',index_col=[0])
df_neighborhoods.head()

Postal Code      Borough                            Neighborhood
0         M1B  Scarborough                          Malvern, Rouge
1         M1C  Scarborough  Rouge Hill, Port Union, Highland Creek
2         M1E  Scarborough       Guildwood, Morningside, West Hill
3         M1G  Scarborough                                  Woburn
4         M1H  Scarborough                               Cedarbrae

In [23]:
# Make sure both dataframes have the same 
df_coordinates.rename(columns={'Postal Code': 'PostalCode'}, inplace=True)
df_neighborhoods.rename(columns={'Postal Code': 'PostalCode'}, inplace=True)

In [24]:
# Merge both datasets
df_neighborhoods_coordinates = pd.merge(df_neighborhoods, df_coordinates, on='PostalCode')
df_neighborhoods_coordinates.head()

PostalCode      Borough                            Neighborhood   Latitude  \
0        M1B  Scarborough                          Malvern, Rouge  43.806686   
1        M1C  Scarborough  Rouge Hill, Port Union, Highland Creek  43.784535   
2        M1E  Scarborough       Guildwood, Morningside, West Hill  43.763573   
3        M1G  Scarborough                                  Woburn  43.770992   
4        M1H  Scarborough                               Cedarbrae  43.773136   

   Longitude  
0 -79.194353  
1 -79.160497  
2 -79.188711  
3 -79.216917  
4 -79.239476

In [25]:
# Check coordinates for a couple of neighborhoods
df_neighborhoods_coordinates[(df_neighborhoods_coordinates['PostalCode']=='M5G') |
                             (df_neighborhoods_coordinates['PostalCode']=='M2H') ]

PostalCode           Borough        Neighborhood   Latitude  Longitude
17        M2H        North York   Hillcrest Village  43.803762 -79.363452
57        M5G  Downtown Toronto  Central Bay Street  43.657952 -79.387383

In [26]:
#Export to .CSV
df_neighborhoods_coordinates.to_csv('Toronto_Postcodes_2.csv')

In [27]:
# Read .csv file from above
df = pd.read_csv('Toronto_Postcodes_2.csv', index_col=0)
df.head()

PostalCode      Borough                            Neighborhood   Latitude  \
0        M1B  Scarborough                          Malvern, Rouge  43.806686   
1        M1C  Scarborough  Rouge Hill, Port Union, Highland Creek  43.784535   
2        M1E  Scarborough       Guildwood, Morningside, West Hill  43.763573   
3        M1G  Scarborough                                  Woburn  43.770992   
4        M1H  Scarborough                               Cedarbrae  43.773136   

   Longitude  
0 -79.194353  
1 -79.160497  
2 -79.188711  
3 -79.216917  
4 -79.239476

In [29]:
# Number of Boroughs and Neighborhoods
print('The dataframe has {} boroughs and {} neighborhoods.'.format(
        len(df['Borough'].unique()),
        df.shape[0]
    )
)

The dataframe has 10 boroughs and 103 neighborhoods.


In [31]:
#count Bourough and Neighborhood
df.groupby('Borough').count()['Neighborhood']

Borough
Central Toronto      9
Downtown Toronto    19
East Toronto         5
East York            5
Etobicoke           12
Mississauga          1
North York          24
Scarborough         17
West Toronto         6
York                 5
Name: Neighborhood, dtype: int64

In [32]:
df_toronto = df[df['Borough'].str.contains('Toronto')]
df_toronto.reset_index(inplace=True)
df_toronto.drop('index', axis=1, inplace=True)
df_toronto.head()

/home/jupyterlab/conda/envs/python/lib/python3.6/site-packages/pandas/core/frame.py:3997: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  errors=errors,


PostalCode          Borough                    Neighborhood   Latitude  \
0        M4E     East Toronto                     The Beaches  43.676357   
1        M4K     East Toronto    The Danforth West, Riverdale  43.679557   
2        M4L     East Toronto  India Bazaar, The Beaches West  43.668999   
3        M4M     East Toronto                 Studio District  43.659526   
4        M4N  Central Toronto                   Lawrence Park  43.728020   

   Longitude  
0 -79.293031  
1 -79.352188  
2 -79.315572  
3 -79.340923  
4 -79.388790

In [33]:
#Check the number of neighborhoods
print(df_toronto.groupby('Borough').count()['Neighborhood'])

Borough
Central Toronto      9
Downtown Toronto    19
East Toronto         5
West Toronto         6
Name: Neighborhood, dtype: int64


In [34]:
#Create list with the Boroughs (to be used later)
boroughs = df_toronto['Borough'].unique().tolist()

In [35]:
#Obtain the coordinates from the dataset itself, just averaging Latitude/Longitude of the current dataset 
lat_toronto = df_toronto['Latitude'].mean()
lon_toronto = df_toronto['Longitude'].mean()
print('The geographical coordinates of Toronto are {}, {}'.format(lat_toronto, lon_toronto))

The geographical coordinates of Toronto are 43.66713498717947, -79.38987324871795


In [38]:
borough_color = {}
for borough in boroughs:
    borough_color[borough]= '#%02X%02X%02X' % tuple(np.random.choice(range(256), size=3)) #Random color

In [93]:
import folium

# create map of Toronto using latitude and longitude values
map_toronto = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood in zip(df_toronto['Latitude'], df_toronto['Longitude'], df_toronto['Borough'], df_toronto['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7).add_to(map_toronto)  
    
map_toronto

# 11. Utilize Geopy to get the coordinates of Toronto

In [40]:
address = 'Toronto'

geolocator = Nominatim(user_agent="my-application")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Toronto are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Toronto are 43.6534817, -79.3839347.


# 14. Use the Foursquare API to explore the neighborhoods

In [48]:
CLIENT_ID = '0NMCGGAMKJKVOHXER43RJQXAHYOHFEUCB2DLDNWEBR5JBNKN' # your Foursquare ID
CLIENT_SECRET = 'HIE2RREPWBSGSBE3LB5OOHV5NWXNHDG4AGTIEMLD0RZ3MHFT' # your Foursquare Secret
VERSION = '20200521' #Foursquare API version
LIMIT = 100 # limit of number of venues returned by Foursquare API
radius = 500 # define radius

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: 0NMCGGAMKJKVOHXER43RJQXAHYOHFEUCB2DLDNWEBR5JBNKN
CLIENT_SECRET:HIE2RREPWBSGSBE3LB5OOHV5NWXNHDG4AGTIEMLD0RZ3MHFT


# 15. Top 100 places within 500 meters

In [49]:
def getVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [50]:
#Get venues for all neighborhoods in our dataset
toronto_venues = getVenues(names=df_toronto['Neighborhood'],
                                latitudes=df_toronto['Latitude'],
                                longitudes=df_toronto['Longitude'])

The Beaches
The Danforth West, Riverdale
India Bazaar, The Beaches West
Studio District
Lawrence Park
Davisville North
North Toronto West
Davisville
Moore Park, Summerhill East
Summerhill West, Rathnelly, South Hill, Forest Hill SE, Deer Park
Rosedale
St. James Town, Cabbagetown
Church and Wellesley
Regent Park, Harbourfront
Garden District, Ryerson
St. James Town
Berczy Park
Central Bay Street
Richmond, Adelaide, King
Harbourfront East, Union Station, Toronto Islands
Toronto Dominion Centre, Design Exchange
Commerce Court, Victoria Hotel
Roselawn
Forest Hill North & West
The Annex, North Midtown, Yorkville
University of Toronto, Harbord
Kensington Market, Chinatown, Grange Park
CN Tower, King and Spadina, Railway Lands, Harbourfront West, Bathurst Quay, South Niagara, Island airport
Stn A PO Boxes
First Canadian Place, Underground city
Christie
Dufferin, Dovercourt Village
Little Portugal, Trinity
Brockton, Parkdale Village, Exhibition Place
High Park, The Junction South
Parkdale, Ron

In [55]:
#Check size of resulting dataframe
toronto_venues.shape

(1623, 7)

In [56]:
toronto_venues.head()

Neighborhood  Neighborhood Latitude  \
0                   The Beaches              43.676357   
1                   The Beaches              43.676357   
2                   The Beaches              43.676357   
3                   The Beaches              43.676357   
4  The Danforth West, Riverdale              43.679557   

   Neighborhood Longitude                               Venue  Venue Latitude  \
0              -79.293031                   Glen Manor Ravine       43.676821   
1              -79.293031  The Big Carrot Natural Food Market       43.678879   
2              -79.293031                 Grover Pub and Grub       43.679181   
3              -79.293031                       Upper Beaches       43.680563   
4              -79.352188                       MenEssentials       43.677820   

   Venue Longitude     Venue Category  
0       -79.293942              Trail  
1       -79.297734  Health Food Store  
2       -79.297215                Pub  
3       -79.292869       Neighborhood  
4       -79.351265     Cosmetics Shop

In [57]:
# Number of venues per neighborhood
toronto_venues.groupby('Neighborhood').count()

Neighborhood Latitude  \
Neighborhood                                                                
Berczy Park                                                            55   
Brockton, Parkdale Village, Exhibition Place                           22   
Business reply mail Processing Centre                                  19   
CN Tower, King and Spadina, Railway Lands, Harb...                     16   
Central Bay Street                                                     66   
Christie                                                               17   
Church and Wellesley                                                   76   
Commerce Court, Victoria Hotel                                        100   
Davisville                                                             34   
Davisville North                                                        9   
Dufferin, Dovercourt Village                                           16   
First Canadian Place, Underground city                                100   
Forest Hill North & West                                                5   
Garden District, Ryerson                                              100   
Harbourfront East, Union Station, Toronto Islands                     100   
High Park, The Junction South                                          23   
India Bazaar, The Beaches West                                         23   
Kensington Market, Chinatown, Grange Park                              57   
Lawrence Park                                                           3   
Little Portugal, Trinity                                               43   
Moore Park, Summerhill East                                             2   
North Toronto West                                                     22   
Parkdale, Roncesvalles                                                 14   
Queen's Park, Ontario Provincial Government                            34   
Regent Park, Harbourfront                                              47   
Richmond, Adelaide, King                                               93   
Rosedale                                                                4   
Roselawn                                                                3   
Runnymede, Swansea                                                     37   
St. James Town                                                         76   
St. James Town, Cabbagetown                                            51   
Stn A PO Boxes                                                         93   
Studio District                                                        40   
Summerhill West, Rathnelly, South Hill, Forest ...                     16   
The Annex, North Midtown, Yorkville                                    26   
The Beaches                                                             4   
The Danforth West, Riverdale                                           42   
Toronto Dominion Centre, Design Exchange                              100   
University of Toronto, Harbord                                         35   

                                                    Neighborhood Longitude  \
Neighborhood                                                                 
Berczy Park                                                             55   
Brockton, Parkdale Village, Exhibition Place                            22   
Business reply mail Processing Centre                                   19   
CN Tower, King and Spadina, Railway Lands, Harb...                      16   
Central Bay Street                                                      66   
Christie                                                                17   
Church and Wellesley                                                    76   
Commerce Court, Victoria Hotel                                         100   
Davisville                                                              34   
Davisville North                    

# 16. Number of Unique Categories

In [59]:
#Number of unique venue categories
print('There are {} uniques categories.'.format(len(toronto_venues['Venue Category'].unique())))

There are 242 uniques categories.


In [60]:
#print out the list of categories
toronto_venues['Venue Category'].unique()[:100]

array(['Trail', 'Health Food Store', 'Pub', 'Neighborhood',
       'Cosmetics Shop', 'Greek Restaurant', 'Italian Restaurant',
       'Ice Cream Shop', 'Yoga Studio', 'Brewery',
       'Fruit & Vegetable Store', 'Dessert Shop', 'Restaurant',
       'Pizza Place', 'Juice Bar', 'Bookstore', 'Bubble Tea Shop',
       'Furniture / Home Store', 'Grocery Store', 'Spa', 'Coffee Shop',
       'Bakery', 'Caribbean Restaurant', 'Café', 'Indian Restaurant',
       'Lounge', 'Frozen Yogurt Shop', 'American Restaurant',
       'Liquor Store', 'Gym', 'Fish & Chips Shop', 'Fast Food Restaurant',
       'Sushi Restaurant', 'Park', 'Pet Store', 'Steakhouse',
       'Burrito Place', 'Movie Theater', 'Sandwich Place', 'Intersection',
       'Food & Drink Shop', 'Fish Market', 'Gay Bar',
       'Seafood Restaurant', 'Cheese Shop', 'Middle Eastern Restaurant',
       'Comfort Food Restaurant', 'Stationery Store', 'Wine Bar',
       'Thai Restaurant', 'Coworking Space', 'Latin American Restaurant',
       '

In [62]:
# check if the results contain "Grocery Store or Vegetable Store"
"Grocery Store","Fruit & Vegetable Store" in toronto_venues['Venue Category'].unique()

('Grocery Store', True)

# 17. Analyze Each Area

In [63]:
# one hot encoding
to_onehot = pd.get_dummies(toronto_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
to_onehot['Neighborhoods'] = toronto_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [to_onehot.columns[-1]] + list(to_onehot.columns[:-1])
to_onehot = to_onehot[fixed_columns]

print(to_onehot.shape)
to_onehot.head()

(1623, 243)


Neighborhoods  Accessories Store  Afghan Restaurant  \
0                   The Beaches                  0                  0   
1                   The Beaches                  0                  0   
2                   The Beaches                  0                  0   
3                   The Beaches                  0                  0   
4  The Danforth West, Riverdale                  0                  0   

   Airport  Airport Food Court  Airport Gate  Airport Lounge  Airport Service  \
0        0                   0             0               0                0   
1        0                   0             0               0                0   
2        0                   0             0               0                0   
3        0                   0             0               0                0   
4        0                   0             0               0                0   

   Airport Terminal  American Restaurant  Antique Shop  Aquarium  Art Gallery  \
0                 0                    0             0         0            0   
1                 0                    0             0         0            0   
2                 0                    0             0         0            0   
3                 0                    0             0         0            0   
4                 0                    0             0         0            0   

   Art Museum  Arts & Crafts Store  Asian Restaurant  Athletics & Sports  \
0           0                    0                 0                   0   
1           0                    0                 0                   0   
2           0                    0                 0                   0   
3           0                    0                 0                   0   
4           0                    0                 0                   0   

   Auto Workshop  BBQ Joint  Baby Store  Bagel Shop  Bakery  Bank  Bar  \
0              0          0           0           0       0     0    0   
1              0          0           0           0       0     0    0   
2              0          0           0           0       0     0    0   
3              0          0           0           0       0     0    0   
4              0          0           0           0       0     0    0   

   Baseball Stadium  Basketball Stadium  Beach  Bed & Breakfast  Beer Bar  \
0                 0                   0      0                0         0   
1                 0                   0      0                0         0   
2                 0                   0      0                0         0   
3                 0                   0      0                0         0   
4                 0                   0      0                0         0   

   Beer Store  Belgian Restaurant  Bistro  Boat or Ferry  Bookstore  Boutique  \
0           0                   0       0              0          0         0   
1           0                   0       0              0          0         0   
2           0                   0       0              0          0         0   
3           0                   0       0              0          0         0   
4           0                   0       0              0          0         0   

   Brazilian Restaurant  Breakfast Spot  Brewery  Bubble Tea Shop  Building  \
0                     0               0        0                0         0   
1                     0               0        0                0         0   
2                     0               0        0                0         0   
3                     0               0        0                0         0   
4                     0               0        0                0         0   

   Burger Joint  Burrito Place  Bus Line  Butcher  Café  \
0             0              0         0        0     0   
1             0              0         0        0     0   
2             0              0         0        0     0   
3             0              0         0  

# 18. Groupby Neighbourhood

In [64]:
to_grouped = to_onehot.groupby(["Neighborhoods"]).mean().reset_index()

print(to_grouped.shape)
to_grouped

(39, 243)


Neighborhoods  Accessories Store  \
0                                         Berczy Park           0.000000   
1        Brockton, Parkdale Village, Exhibition Place           0.000000   
2               Business reply mail Processing Centre           0.000000   
3   CN Tower, King and Spadina, Railway Lands, Har...           0.000000   
4                                  Central Bay Street           0.000000   
5                                            Christie           0.000000   
6                                Church and Wellesley           0.000000   
7                      Commerce Court, Victoria Hotel           0.000000   
8                                          Davisville           0.000000   
9                                    Davisville North           0.000000   
10                       Dufferin, Dovercourt Village           0.000000   
11             First Canadian Place, Underground city           0.000000   
12                           Forest Hill North & West           0.000000   
13                           Garden District, Ryerson           0.000000   
14  Harbourfront East, Union Station, Toronto Islands           0.000000   
15                      High Park, The Junction South           0.000000   
16                     India Bazaar, The Beaches West           0.000000   
17          Kensington Market, Chinatown, Grange Park           0.000000   
18                                      Lawrence Park           0.000000   
19                           Little Portugal, Trinity           0.000000   
20                        Moore Park, Summerhill East           0.000000   
21                                 North Toronto West           0.000000   
22                             Parkdale, Roncesvalles           0.000000   
23        Queen's Park, Ontario Provincial Government           0.000000   
24                          Regent Park, Harbourfront           0.000000   
25                           Richmond, Adelaide, King           0.010753   
26                                           Rosedale           0.000000   
27                                           Roselawn           0.000000   
28                                 Runnymede, Swansea           0.000000   
29                                     St. James Town           0.000000   
30                        St. James Town, Cabbagetown           0.000000   
31                                     Stn A PO Boxes           0.000000   
32                                    Studio District           0.000000   
33  Summerhill West, Rathnelly, South Hill, Forest...           0.000000   
34                The Annex, North Midtown, Yorkville           0.000000   
35                                        The Beaches           0.000000   
36                       The Danforth West, Riverdale           0.000000   
37           Toronto Dominion Centre, Design Exchange           0.000000   
38                     University of Toronto, Harbord           0.000000   

    Afghan Restaurant  Airport  Airport Food Court  Airport Gate  \
0            0.000000   0.0000              0.0000        0.0000   
1            0.000000   0.0000              0.0000        0.0000   
2            0.000000   0.0000              0.0000        0.0000   
3            0.000000   0.0625              0.0625        0.0625   
4            0.000000   0.0000              0.0000        0.0000   
5            0.000000   0.0000              0.0000        0.0000   
6            0.013158   0.0000              0.0000        0.0000   
7            0.000000   0.0000              0.0000        0.0000   
8            0.000000   0.0000              0.0000        0.0000   
9            0.000000   0.0000              0.0000        0.0000   
10           0.000000   0.0000              0.0000        0.0000   
11           0.000000   0.0000              0.0000        0.0000   
12           0.000000   0.0000              0.0000        0.0000   
13           0.000000   0.0000              0.0

In [74]:
len(to_grouped[to_grouped["Grocery Store"] > 0])

12

In [75]:
len(to_grouped[to_grouped["Farmers Market"] > 0])

7

In [76]:
len(to_grouped[to_grouped["Juice Bar"] > 0])

6

In [77]:
len(to_grouped[to_grouped["Market"] > 0])

1

In [140]:
to_asian = to_grouped[["Neighborhoods","Grocery Store"]]
# grocery_store = to_grouped[["Neighborhoods","Grocery Store"]]

In [141]:
to_asian.head()
# grocery_store.head()

Neighborhoods  Grocery Store
0                                        Berczy Park       0.018182
1       Brockton, Parkdale Village, Exhibition Place       0.045455
2              Business reply mail Processing Centre       0.000000
3  CN Tower, King and Spadina, Railway Lands, Har...       0.000000
4                                 Central Bay Street       0.000000

# 20. Implement K-Means for Clustering

In [142]:
# set number of clusters
toclusters = 3

to_clustering = to_asian.drop(["Neighborhoods"], 1)

# run k-means clustering
kmeans = KMeans(n_clusters=toclusters, random_state=0).fit(to_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10]

array([0, 2, 0, 0, 0, 1, 0, 0, 0, 0], dtype=int32)

In [143]:
# create a new dataframe that includes the cluster as well as the top 10 venues for each neighborhood.
to_merged = to_asian.copy()

# add clustering labels
to_merged["Cluster Labels"] = kmeans.labels_

In [144]:
to_merged.rename(columns={"Neighborhoods": "Neighborhood"}, inplace=True)
to_merged.head()

Neighborhood  Grocery Store  \
0                                        Berczy Park       0.018182   
1       Brockton, Parkdale Village, Exhibition Place       0.045455   
2              Business reply mail Processing Centre       0.000000   
3  CN Tower, King and Spadina, Railway Lands, Har...       0.000000   
4                                 Central Bay Street       0.000000   

   Cluster Labels  
0               0  
1               2  
2               0  
3               0  
4               0

In [145]:
# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
to_merged = to_merged.join(toronto_venues.set_index("Neighborhood"), on="Neighborhood")

print(to_merged.shape)
to_merged.head()

(1623, 9)


Neighborhood  Grocery Store  Cluster Labels  Neighborhood Latitude  \
0  Berczy Park       0.018182               0              43.644771   
0  Berczy Park       0.018182               0              43.644771   
0  Berczy Park       0.018182               0              43.644771   
0  Berczy Park       0.018182               0              43.644771   
0  Berczy Park       0.018182               0              43.644771   

   Neighborhood Longitude                                      Venue  \
0              -79.373306                                       LCBO   
0              -79.373306       The Keg Steakhouse + Bar - Esplanade   
0              -79.373306                             Fresh On Front   
0              -79.373306                              Meridian Hall   
0              -79.373306  Hockey Hall Of Fame (Hockey Hall of Fame)   

   Venue Latitude  Venue Longitude                 Venue Category  
0       43.642944       -79.372440                   Liquor Store  
0       43.646712       -79.374768                     Restaurant  
0       43.647815       -79.374453  Vegetarian / Vegan Restaurant  
0       43.646292       -79.376022                   Concert Hall  
0       43.646974       -79.377323                         Museum

In [ ]:
# sort the results by Cluster Labels
print(to_merged.shape)
to_merged.sort_values(["Cluster Labels"], inplace=True)
to_merged

# 21. Visualize Clusters on a Map

In [161]:
# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors
import folium

In [162]:
# create map
map_clusters = folium.Map(location=[lat_toronto, lon_toronto], zoom_start=11)

# set color scheme for the clusters
x = np.arange(toclusters)
ys = [i+x+(i*x)**2 for i in range(toclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(to_merged['Neighborhood Latitude'], to_merged['Neighborhood Longitude'], to_merged['Neighborhood'], to_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' - Cluster ' + str(cluster))
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

In [163]:
# save the map as HTML file
map_clusters.save('map_clusters.html')

# Examine Clusters

In [164]:
#Cluster 0
to_merged.loc[to_merged['Cluster Labels'] == 0]

Neighborhood  Grocery Store  \
0                                         Berczy Park       0.018182   
3   CN Tower, King and Spadina, Railway Lands, Har...       0.000000   
3   CN Tower, King and Spadina, Railway Lands, Har...       0.000000   
3   CN Tower, King and Spadina, Railway Lands, Har...       0.000000   
3   CN Tower, King and Spadina, Railway Lands, Har...       0.000000   
3   CN Tower, King and Spadina, Railway Lands, Har...       0.000000   
3   CN Tower, King and Spadina, Railway Lands, Har...       0.000000   
3   CN Tower, King and Spadina, Railway Lands, Har...       0.000000   
3   CN Tower, King and Spadina, Railway Lands, Har...       0.000000   
4                                  Central Bay Street       0.000000   
2               Business reply mail Processing Centre       0.000000   
2               Business reply mail Processing Centre       0.000000   
2               Business reply mail Processing Centre       0.000000   
2               Business reply mail Processing Centre       0.000000   
0                                         Berczy Park       0.018182   
0                                         Berczy Park       0.018182   
0                                         Berczy Park       0.018182   
0                                         Berczy Park       0.018182   
0                                         Berczy Park       0.018182   
0                                         Berczy Park       0.018182   
0                                         Berczy Park       0.018182   
3   CN Tower, King and Spadina, Railway Lands, Har...       0.000000   
3   CN Tower, King and Spadina, Railway Lands, Har...       0.000000   
3   CN Tower, King and Spadina, Railway Lands, Har...       0.000000   
0                                         Berczy Park       0.018182   
0                                         Berczy Park       0.018182   
0                                         Berczy Park       0.018182   
0                                         Berczy Park       0.018182   
0                                         Berczy Park       0.018182   
0                                         Berczy Park       0.018182   
0                                         Berczy Park       0.018182   
0                                         Berczy Park       0.018182   
0                                         Berczy Park       0.018182   
0                                         Berczy Park       0.018182   
0                                         Berczy Park       0.018182   
4                                  Central Bay Street       0.000000   
3   CN Tower, King and Spadina, Railway Lands, Har...       0.000000   
2               Business reply mail Processing Centre       0.000000   
2               Business reply mail Processing Centre       0.000000   
2               Business reply mail Processing Centre       0.000000   
3   CN Tower, King and Spadina, Railway Lands, Har...       0.000000   
3   CN Tower, King and Spadina, Railway Lands, Har...       0.000000   
3   CN Tower, King and Spadina, Railway Lands, Har...       0.000000   
3   CN Tower, King and Spadina, Railway Lands, Har...       0.000000   
0                                         Berczy Park       0.018182   
2               Business reply mail Processing Centre       0.000000   
2               Business reply mail Processing Centre       0.000000   
2               Business reply mail Processing Centre       0.000000   
7                      Commerce Court, Victoria Hotel       0.000000   
7                      Commerce Court, Victoria Hotel       0.000000   
7                      Commerce Court, Victoria Hotel       0.000000   
7                      Commerce Court, Victoria Hotel       0.000000   
7                      Commerce Court, Victoria Hotel       0.000000   
7                      Commerce Court, Victoria Hotel       0.000000   
7                      Commerce Court, Victoria Hotel       0.000000   
7        

In [152]:
#Cluster 1
to_merged.loc[to_merged['Cluster Labels'] == 1]

Neighborhood  Grocery Store  Cluster Labels  Neighborhood Latitude  \
5     Christie       0.235294               1              43.669542   
5     Christie       0.235294               1              43.669542   
5     Christie       0.235294               1              43.669542   
5     Christie       0.235294               1              43.669542   
5     Christie       0.235294               1              43.669542   
5     Christie       0.235294               1              43.669542   
5     Christie       0.235294               1              43.669542   
5     Christie       0.235294               1              43.669542   
5     Christie       0.235294               1              43.669542   
5     Christie       0.235294               1              43.669542   
5     Christie       0.235294               1              43.669542   
5     Christie       0.235294               1              43.669542   
5     Christie       0.235294               1              43.669542   
5     Christie       0.235294               1              43.669542   
5     Christie       0.235294               1              43.669542   
5     Christie       0.235294               1              43.669542   
5     Christie       0.235294               1              43.669542   

   Neighborhood Longitude                 Venue  Venue Latitude  \
5              -79.422564          Dupont Disco       43.670490   
5              -79.422564   Garrison Creek Park       43.671690   
5              -79.422564          Foto Grocery       43.667979   
5              -79.422564           Contra Cafe       43.669107   
5              -79.422564        Vinny’s Panini       43.670679   
5              -79.422564             Starbucks       43.671530   
5              -79.422564  Scout and Cash Caffe       43.667360   
5              -79.422564       Universal Grill       43.670550   
5              -79.422564           Faema Caffe       43.671046   
5              -79.422564          Fiesta Farms       43.668471   
5              -79.422564     Stubbe Chocolates       43.671566   
5              -79.422564               Loblaws       43.671657   
5              -79.422564         Sobeys Dupont       43.670977   
5              -79.422564  Marlenes Just Babies       43.671824   
5              -79.422564           Queens Club       43.672386   
5              -79.422564            Actinolite       43.667858   
5              -79.422564     Marian Engel Park       43.673754   

   Venue Longitude      Venue Category  
5       -79.426611           Nightclub  
5       -79.427805                Park  
5       -79.428217       Grocery Store  
5       -79.426105                Café  
5       -79.426148  Italian Restaurant  
5       -79.421400         Coffee Shop  
5       -79.419938                Café  
5       -79.426541               Diner  
5       -79.419297                Café  
5       -79.420485       Grocery Store  
5       -79.421289         Candy Store  
5       -79.421364       Grocery Store  
5       -79.427573       Grocery Store  
5       -79.420499          Baby Store  
5       -79.418106  Athletics & Sports  
5       -79.428054          Restaurant  
5       -79.423988                Park

In [ ]:
#Cluster 2
to_merged.loc[to_merged['Cluster Labels'] == 2]

# 22. Final Observations

Most of the Categories are in Cluster 1 and 2. The neighborhoods in Cluster 1 and 2 are densely occupied by Grocery Stores and Restaurants and are near by various other locations.
There are very few Grocery Stores in Cluster 3 in the neighborhood of Christie. According to the location data and nearby venues, it is less competitive and more probability of Success in the neighborhood of Christie for opening up a new Indian Grocery Store.

### This notebook is partly derived from our New York lab and Assignment Week 3 Toronto lab.